In [1]:

import tensorflow as tf
print("TensorFlow version:", tf.__version__) 

C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\tensorflow\python\framework\dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\tensorflow\python\framework\dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\tensorflow\python\framework\dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([

TensorFlow version: 1.13.1


In [2]:
use_device='/gpu:0'


import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import keras

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Embedding, Conv1D, GlobalMaxPooling1D, Dense, Input, Concatenate
from tensorflow.keras.layers import LSTM

from tensorflow.python.client import device_lib

#import models and layers from tensorflow.keras to avoid errors like "TypeError: Checkpointable._track_checkpointable()"
from tensorflow.keras.models import Model

from tensorflow.keras.layers import Dropout, Activation, Flatten
from keras.optimizers import Adam
    
from tensorflow.keras.preprocessing import image
from tensorflow.keras.preprocessing.image import ImageDataGenerator
    
from keras.utils import layer_utils
from keras.utils.data_utils import get_file
from keras.applications.imagenet_utils import preprocess_input
from IPython.display import SVG
from keras.utils.vis_utils import model_to_dot
from keras.utils import plot_model
#import tensorflow.keras.backend as K
from keras import regularizers
    
import pickle
import pandas as pd

from datetime import datetime

from sklearn.model_selection import train_test_split
    
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

Using TensorFlow backend.
C:\Users\Alejandro 2\Anaconda3\envs\original_v1_1\envs\original_v1_0\lib\site-packages\sklearn\utils\validation.py:37: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  LARGE_SPARSE_SUPPORTED = LooseVersion(scipy_version) >= '0.14.0'


[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 9924410289705465632
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 517944114
locality {
  bus_id: 1
  links {
  }
}
incarnation: 7200708544332493161
physical_device_desc: "device: 0, name: NVIDIA GeForce GTX 1650, pci bus id: 0000:01:00.0, compute capability: 7.5"
]


In [3]:
        
# define paths for saving results and other data
#---------------------------------------------------------------------------------------------------------------------    
path_data= "xxx" #where is the dataset
path_data_2= "xxx""



X1_import=path_data_2 + "SMILES_X1.txt" #where is the Xdata of the dataset (SMILES)
X2_import=path_data_2 + "SMILES_X2.txt"
# Load the saved numeric arrays from the file
Y_import=path_data_2 + "X.txt" #where is the Ydata of the dataset (property to predict)
   

# Load SMILES strings from file
with open(X1_import, 'r') as f:
    smiles_data_1 = f.readlines()
with open(X2_import, 'r') as f:
    smiles_data_2 = f.readlines()

# Load properties from file
with open(Y_import, 'r') as f:
    X_data = f.readlines()
    
print(smiles_data_1[10])
print(smiles_data_2[10])
print(X_data[10])

C=CCC

CCCCCCCC

0.31



In [9]:
# Split the dataset into train and test sets
# Load the tokenizer
tokenizer_path = path_data_2 + 'tokenizer_all.pkl'
with open(tokenizer_path, 'rb') as f:
    tokenizer_all = pickle.load(f)


sequences_1 = tokenizer_all.texts_to_sequences(smiles_data_1)
max_length_1 = max(len(seq) for seq in sequences_1)
padded_sequences_1 = pad_sequences(sequences_1, maxlen=max_length_1, padding='post')
print(np.shape(padded_sequences_1))


sequences_2 = tokenizer_all.texts_to_sequences(smiles_data_2)
max_length_2 = max(len(seq) for seq in sequences_2)
padded_sequences_2 = pad_sequences(sequences_2, maxlen=max_length_2, padding='post')
print(np.shape(padded_sequences_2))

# Convert property data to numpy array
X_labels = np.array([float(prop.strip()) for prop in X_data])

# Define vocabulary size for SMILES_1
vocab_size_1 = len(tokenizer_all.word_index) + 1


# Define vocabulary size for SMILES_2
vocab_size_2 = len(tokenizer_all.word_index) + 1


# Define embedding dimension
embedding_dim = 128

# Split the dataset into train and test sets
test_size = 0.8
random_state = 42
X_train_1, X_test_1, X_train_2, X_test_2, y_train, y_test = train_test_split(
    padded_sequences_1, padded_sequences_2, X_labels, test_size=test_size, random_state=random_state)
print(np.shape(X_train_1))
print(np.shape(X_train_2))
print(np.shape(X_test_1))
print(np.shape(X_test_2))

(736, 48)
(736, 45)
(147, 48)
(147, 45)
(589, 48)
(589, 45)


In [10]:
#save X_test_1 and y_test to .npy file

np.save(path_data_2 + 'X_test_0.npy', X_test_1)
np.save(path_data_2 + 'X_test_1.npy', X_test_2)
np.save(path_data_2 + 'y_test.npy', y_test)

In [11]:
from keras.callbacks import Callback   
    
# checkpoint_filepath = path_data_2 + "Weights.npy" #'checkpoint'
monitor_custom='val_mean_absolute_error' #val_mean_absolute_error   val_mean_absolute_percentage_error
mode_custom='min'


early_stop= tf.keras.callbacks.EarlyStopping(monitor=monitor_custom,  verbose=3,
                                             mode=mode_custom, patience=1000, restore_best_weights=True)
# callback_list= [model_checkpoint_callback, reduce_lr, early_stop]
callback_list= [early_stop]




def Model_embeddings(X_train_1, X_train_2, y_train, vocab_size_1, vocab_size_2, embedding_dim, max_length_1, max_length_2,
                     ep, b_s, v_s, shuffle_dataset, alpha, NeuronsFC, w1, w2, w3, channels_1, channels_2, 
                     channels_3, lr, beta_1, beta_2, epsilon, decay, amsgrad):

    
    # Create input shapes
    input_shape1 = X_train_1.shape[1:]
    input_shape2 = X_train_2.shape[1:]
    # Define inputs
    A_input = Input(shape=input_shape1, name='INPUT')
    A2_input = Input(shape=input_shape2, name='INPUT_2')
    concatenated = tf.keras.layers.concatenate([A_input, A2_input])
    merged = Dense(NeuronsFC)(concatenated)
    merged = tf.keras.layers.LeakyReLU(alpha)(merged)
    output_layer = Dense(1, activation='linear')(merged)
    # Create model
    model = Model(inputs=[A_input, A2_input], outputs=output_layer)
    print(model.summary(line_length=None, positions=None, print_fn=None))
    # Compile model
    opt = tf.keras.optimizers.Adam(lr, beta_1, beta_2, epsilon, decay, amsgrad)
    model.compile(loss='mean_absolute_error', optimizer=opt,
                           metrics=['mean_absolute_error', 'mean_absolute_percentage_error'])
    Data_X=[X_train_1, X_train_2]
    # Train the model
    HISTORY = model.fit(Data_X, y_train, epochs=ep, batch_size=b_s, validation_split=v_s,
              shuffle=shuffle_dataset, callbacks=callback_list)
    
    return model, HISTORY

In [12]:
#DATA=====================================================================================================
Mode=0
#NUMBER OF TEST===========================================================================================
number_of_test = 1
#FREEZE_LAYERS============================================================================================
is_trainable_conv1_1=True #
is_trainable_conv1_2=True #
is_trainable_conv1_3=True #
is_trainable_conv1_4=True #
is_trainable_conv1_5=True
is_trainable_HIDDEN_A1_0=True #the CNN input side of the ANN
is_trainable_HIDDEN_A2_0=True #the Hbonds input side of the ANN (1:True, 2:True, 2:False)
is_trainable_HIDDEN_FC_all=True #concatenated FCs
#HYPERPARAMETERS==========================================================================================
lr=[0.01, 0.001, 0.0001]
beta_1=0.99
beta_2=0.999
epsilon=None
decay=0
amsgrad=True
b_s=[1000, 100, 50, 20]
samples_on_control=0
samples_on_test=200
v_s= 0.2 #(samples_on_test+samples_on_control)/number_of_samples_X   
shuffle_dataset="False"
Drop_prob=0.2
alpha=0.05
reg=0.01
#WORKING PARAMETERS======================================================================================
number_epochs=6000 #
#FULLY CONNECTED=========================================================================================
NeuronsFC=50 # neurons combined FC
NeuronsFC_A2=5 #neurons in the Hbonds input
NeuronsFC_A1=5 #neurons in the CNN input
#CNN=====================================================================================================
w1=1 # must be the same if the model has been pre-trained
w2=6
w3=10
channels_1=32
channels_2=64
channels_3=128

In [13]:
# Iterate over each combination of learning rate and batch size

counter=0
Results=[]
for i in b_s:
    for j in lr:
        Name_saving="X_embedding_" + str(counter) + str(number_of_test)
        print("model name (to save): " + Name_saving)
        MODEL, HISTORY= Model_embeddings(X_train_1, X_train_2, y_train, vocab_size_1, vocab_size_2, embedding_dim, max_length_1, max_length_2,
                         number_epochs, i, v_s, shuffle_dataset, alpha, NeuronsFC, w1, w2, w3, channels_1, channels_2, channels_3,
                         j, beta_1, beta_2, epsilon, decay, amsgrad)
        #save model
        try:
            MODEL.save(path_data_2 + Name_saving + ".model")
            print("Model saved")
        except:
            print("Model saved?")
            try:
                MODEL.save(path_data_2 + Name_saving + ".model")
                print("Model now saved!")
            except Exception as e:
                print("Error saving model:", e)
            
        # Extract the mean absolute error from the training history
        mean_absolute_error_model = HISTORY.history['mean_absolute_error'][-1]  # Considering the last epoch error
        val_mean_absolute_error_model = HISTORY.history['val_mean_absolute_error'][-1]
        # Append the results to the list
        Results.append([counter, j, i, mean_absolute_error_model, val_mean_absolute_error_model])            
        counter+=1

model name (to save): X_embedding_01
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
INPUT (InputLayer)              (None, 48)           0                                            
__________________________________________________________________________________________________
INPUT_2 (InputLayer)            (None, 45)           0                                            
__________________________________________________________________________________________________
concatenate_10 (Concatenate)    (None, 93)           0           INPUT[0][0]                      
                                                                 INPUT_2[0][0]                    
__________________________________________________________________________________________________
dense_20 (Dense)                (None, 50)           4700        concate

Epoch 26/6000
117/117 [==============================] - 0s 205us/sample - loss: 0.4287 - mean_absolute_error: 0.4287 - mean_absolute_percentage_error: 161.1468 - val_loss: 0.4404 - val_mean_absolute_error: 0.4404 - val_mean_absolute_percentage_error: 226.5554
Epoch 27/6000
117/117 [==============================] - 0s 179us/sample - loss: 0.3617 - mean_absolute_error: 0.3617 - mean_absolute_percentage_error: 112.5724 - val_loss: 0.4456 - val_mean_absolute_error: 0.4456 - val_mean_absolute_percentage_error: 232.1071
Epoch 28/6000
117/117 [==============================] - 0s 282us/sample - loss: 0.3374 - mean_absolute_error: 0.3374 - mean_absolute_percentage_error: 109.1473 - val_loss: 0.4739 - val_mean_absolute_error: 0.4739 - val_mean_absolute_percentage_error: 256.8216
Epoch 29/6000
117/117 [==============================] - 0s 205us/sample - loss: 0.3674 - mean_absolute_error: 0.3674 - mean_absolute_percentage_error: 148.3025 - val_loss: 0.5007 - val_mean_absolute_error: 0.5007 - v

Epoch 58/6000
117/117 [==============================] - 0s 137us/sample - loss: 0.2282 - mean_absolute_error: 0.2282 - mean_absolute_percentage_error: 80.9366 - val_loss: 0.3385 - val_mean_absolute_error: 0.3385 - val_mean_absolute_percentage_error: 190.0426
Epoch 59/6000
117/117 [==============================] - 0s 120us/sample - loss: 0.2302 - mean_absolute_error: 0.2302 - mean_absolute_percentage_error: 83.3928 - val_loss: 0.3401 - val_mean_absolute_error: 0.3401 - val_mean_absolute_percentage_error: 187.0502
Epoch 60/6000
117/117 [==============================] - 0s 145us/sample - loss: 0.2337 - mean_absolute_error: 0.2337 - mean_absolute_percentage_error: 84.8284 - val_loss: 0.3410 - val_mean_absolute_error: 0.3410 - val_mean_absolute_percentage_error: 184.7054
Epoch 61/6000
117/117 [==============================] - 0s 145us/sample - loss: 0.2363 - mean_absolute_error: 0.2363 - mean_absolute_percentage_error: 84.7896 - val_loss: 0.3445 - val_mean_absolute_error: 0.3445 - val_m

Epoch 90/6000
117/117 [==============================] - 0s 137us/sample - loss: 0.1779 - mean_absolute_error: 0.1779 - mean_absolute_percentage_error: 46.9847 - val_loss: 0.3901 - val_mean_absolute_error: 0.3901 - val_mean_absolute_percentage_error: 222.9826
Epoch 91/6000
117/117 [==============================] - 0s 120us/sample - loss: 0.1778 - mean_absolute_error: 0.1778 - mean_absolute_percentage_error: 46.1843 - val_loss: 0.3886 - val_mean_absolute_error: 0.3886 - val_mean_absolute_percentage_error: 223.7401
Epoch 92/6000
117/117 [==============================] - 0s 145us/sample - loss: 0.1774 - mean_absolute_error: 0.1774 - mean_absolute_percentage_error: 45.2050 - val_loss: 0.3869 - val_mean_absolute_error: 0.3869 - val_mean_absolute_percentage_error: 224.4097
Epoch 93/6000
117/117 [==============================] - 0s 111us/sample - loss: 0.1772 - mean_absolute_error: 0.1772 - mean_absolute_percentage_error: 46.2737 - val_loss: 0.3862 - val_mean_absolute_error: 0.3862 - val_m

Epoch 122/6000
117/117 [==============================] - 0s 137us/sample - loss: 0.1461 - mean_absolute_error: 0.1461 - mean_absolute_percentage_error: 53.4280 - val_loss: 0.4464 - val_mean_absolute_error: 0.4464 - val_mean_absolute_percentage_error: 234.5122
Epoch 123/6000
117/117 [==============================] - 0s 137us/sample - loss: 0.1438 - mean_absolute_error: 0.1438 - mean_absolute_percentage_error: 52.0778 - val_loss: 0.4467 - val_mean_absolute_error: 0.4467 - val_mean_absolute_percentage_error: 235.4599
Epoch 124/6000
117/117 [==============================] - 0s 128us/sample - loss: 0.1413 - mean_absolute_error: 0.1413 - mean_absolute_percentage_error: 50.4392 - val_loss: 0.4467 - val_mean_absolute_error: 0.4467 - val_mean_absolute_percentage_error: 236.4909
Epoch 125/6000
117/117 [==============================] - 0s 137us/sample - loss: 0.1389 - mean_absolute_error: 0.1389 - mean_absolute_percentage_error: 48.7338 - val_loss: 0.4461 - val_mean_absolute_error: 0.4461 - v

...

117/117 [==============================] - 0s 650us/sample - loss: 0.0421 - mean_absolute_error: 0.0421 - mean_absolute_percentage_error: 9.5321 - val_loss: 0.4402 - val_mean_absolute_error: 0.4402 - val_mean_absolute_percentage_error: 228.1402
Epoch 1094/6000
117/117 [==============================] - 0s 624us/sample - loss: 0.0417 - mean_absolute_error: 0.0417 - mean_absolute_percentage_error: 9.0850 - val_loss: 0.4404 - val_mean_absolute_error: 0.4404 - val_mean_absolute_percentage_error: 228.2266
Epoch 1095/6000
117/117 [==============================] - 0s 667us/sample - loss: 0.0414 - mean_absolute_error: 0.0414 - mean_absolute_percentage_error: 8.7677 - val_loss: 0.4402 - val_mean_absolute_error: 0.4402 - val_mean_absolute_percentage_error: 227.4369
Epoch 1096/6000
117/117 [==============================] - 0s 641us/sample - loss: 0.0420 - mean_absolute_error: 0.0420 - mean_absolute_percentage_error: 9.0029 - val_loss: 0.4409 - val_mean_absolute_error: 0.4409 - val_mean_absolute

117/117 [==============================] - 0s 701us/sample - loss: 0.0407 - mean_absolute_error: 0.0407 - mean_absolute_percentage_error: 9.6814 - val_loss: 0.4425 - val_mean_absolute_error: 0.4425 - val_mean_absolute_percentage_error: 227.3586
Epoch 1156/6000
117/117 [==============================] - 0s 667us/sample - loss: 0.0410 - mean_absolute_error: 0.0410 - mean_absolute_percentage_error: 9.1984 - val_loss: 0.4421 - val_mean_absolute_error: 0.4421 - val_mean_absolute_percentage_error: 227.6451
Epoch 1157/6000
117/117 [==============================] - 0s 675us/sample - loss: 0.0410 - mean_absolute_error: 0.0410 - mean_absolute_percentage_error: 9.3042 - val_loss: 0.4432 - val_mean_absolute_error: 0.4432 - val_mean_absolute_percentage_error: 229.9280
Epoch 1158/6000
117/117 [==============================] - 0s 624us/sample - loss: 0.0407 - mean_absolute_error: 0.0407 - mean_absolute_percentage_error: 8.9150 - val_loss: 0.4439 - val_mean_absolute_error: 0.4439 - val_mean_absolute

117/117 [==============================] - 0s 709us/sample - loss: 0.0405 - mean_absolute_error: 0.0405 - mean_absolute_percentage_error: 9.6048 - val_loss: 0.4455 - val_mean_absolute_error: 0.4455 - val_mean_absolute_percentage_error: 229.4661
Epoch 1218/6000
117/117 [==============================] - 0s 727us/sample - loss: 0.0426 - mean_absolute_error: 0.0426 - mean_absolute_percentage_error: 9.7318 - val_loss: 0.4445 - val_mean_absolute_error: 0.4445 - val_mean_absolute_percentage_error: 228.9666
Epoch 1219/6000
117/117 [==============================] - 0s 718us/sample - loss: 0.0408 - mean_absolute_error: 0.0408 - mean_absolute_percentage_error: 10.1394 - val_loss: 0.4453 - val_mean_absolute_error: 0.4453 - val_mean_absolute_percentage_error: 231.1773
Epoch 1220/6000
117/117 [==============================] - 0s 684us/sample - loss: 0.0426 - mean_absolute_error: 0.0426 - mean_absolute_percentage_error: 10.7152 - val_loss: 0.4460 - val_mean_absolute_error: 0.4460 - val_mean_absolu

117/117 [==============================] - 0s 675us/sample - loss: 0.0383 - mean_absolute_error: 0.0383 - mean_absolute_percentage_error: 8.4805 - val_loss: 0.4499 - val_mean_absolute_error: 0.4499 - val_mean_absolute_percentage_error: 233.0974
Epoch 1280/6000
117/117 [==============================] - 0s 803us/sample - loss: 0.0376 - mean_absolute_error: 0.0376 - mean_absolute_percentage_error: 8.4834 - val_loss: 0.4495 - val_mean_absolute_error: 0.4495 - val_mean_absolute_percentage_error: 232.4051
Epoch 1281/6000
117/117 [==============================] - 0s 709us/sample - loss: 0.0378 - mean_absolute_error: 0.0378 - mean_absolute_percentage_error: 8.7741 - val_loss: 0.4493 - val_mean_absolute_error: 0.4493 - val_mean_absolute_percentage_error: 232.1025
Epoch 1282/6000
117/117 [==============================] - 0s 727us/sample - loss: 0.0382 - mean_absolute_error: 0.0382 - mean_absolute_percentage_error: 8.7408 - val_loss: 0.4496 - val_mean_absolute_error: 0.4496 - val_mean_absolute

117/117 [==============================] - 0s 624us/sample - loss: 0.0406 - mean_absolute_error: 0.0406 - mean_absolute_percentage_error: 10.0825 - val_loss: 0.4521 - val_mean_absolute_error: 0.4521 - val_mean_absolute_percentage_error: 235.5385
Epoch 1342/6000
117/117 [==============================] - 0s 624us/sample - loss: 0.0404 - mean_absolute_error: 0.0404 - mean_absolute_percentage_error: 9.7774 - val_loss: 0.4502 - val_mean_absolute_error: 0.4502 - val_mean_absolute_percentage_error: 233.1450
Epoch 1343/6000
117/117 [==============================] - 0s 615us/sample - loss: 0.0398 - mean_absolute_error: 0.0398 - mean_absolute_percentage_error: 10.2120 - val_loss: 0.4488 - val_mean_absolute_error: 0.4488 - val_mean_absolute_percentage_error: 231.0871
Epoch 1344/6000
117/117 [==============================] - 0s 633us/sample - loss: 0.0403 - mean_absolute_error: 0.0403 - mean_absolute_percentage_error: 11.4747 - val_loss: 0.4497 - val_mean_absolute_error: 0.4497 - val_mean_absol

In [14]:
#save as excel
#===============

# Define column names for the Excel file
columns = ['Counter', 'lr', 'bs', 'MAE', 'val MAE']
# Convert Results array to a DataFrame
Results_df = pd.DataFrame(Results, columns=columns)
writer = pd.ExcelWriter(path_data_2 + "Results_file_" + str(number_of_test) + ".xlsx", engine='xlsxwriter')
Results_df.to_excel(writer, sheet_name='Results_file_', index=False)
writer.save()

In [15]:
Results_df.head(20)

Counter      lr    bs       MAE   val MAE
0         0  0.0100  1000  0.028243  0.455743
1         1  0.0010  1000  0.030138  0.567183
2         2  0.0001  1000  0.082852  0.519429
3         3  0.0100   100  0.040247  0.481450
4         4  0.0010   100  0.048355  0.510991
5         5  0.0001   100  0.069350  0.510359
6         6  0.0100    50  0.040208  0.486245
7         7  0.0010    50  0.029833  0.476365
8         8  0.0001    50  0.045684  0.491614
9         9  0.0100    20  0.047103  0.382795
10       10  0.0010    20  0.023786  0.493944
11       11  0.0001    20  0.039361  0.452289